In [0]:
from pyspark.sql.functions import lit, cast, col
from pyspark.sql.types import *

In [0]:
# mount data
mount_point = "/mnt/adverse-events"

In [0]:
# unmount if needed
mount_point = mount_point
dbutils.fs.unmount(mount_point)

/mnt/adverse-events has been unmounted.


True

In [0]:
# connect to storage account and containers
configs = {"fs.azure.account.auth.type": "OAuth",
           "fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
           "fs.azure.account.oauth2.client.id": "e99fd849-a6b3-49c5-b7a0-044016a9b700",
           "fs.azure.account.oauth2.client.secret": dbutils.secrets.get(scope = "key-vault-scope", key = "client-secret") ,
           "fs.azure.account.oauth2.client.endpoint": "https://login.microsoftonline.com/62a42a60-1f3b-41ee-92d8-d46ce7b9d9ef/oauth2/token/"}

# mount data
dbutils.fs.mount(
    source = "abfss://adverse-events@adverseeventsa.dfs.core.windows.net",
    mount_point = mount_point,
    extra_configs = configs
)

True

In [0]:
%fs
ls "/mnt/adverse-events/transformed-data/"

path name size modificationTime dbfs:/mnt/adverse-events/transformed-data/dim_action_taken.csv/ dim_action_taken.csv/ 0 1730825044000 dbfs:/mnt/adverse-events/transformed-data/dim_administration_route.csv/ dim_administration_route.csv/ 0 1730825045000 dbfs:/mnt/adverse-events/transformed-data/dim_country_codes.csv/ dim_country_codes.csv/ 0 1730825046000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2015.csv/ dim_drug_information_2015.csv/ 0 1730824646000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2016.csv/ dim_drug_information_2016.csv/ 0 1730827026000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2017.csv/ dim_drug_information_2017.csv/ 0 1730828794000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2018.csv/ dim_drug_information_2018.csv/ 0 1730832360000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2019.csv/ dim_drug_information_2019.csv/ 0 1730836627000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2020.csv/ dim_drug_information_2020.csv/ 0 1730838976000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2021.csv/ dim_drug_information_2021.csv/ 0 1730900480000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2022.csv/ dim_drug_information_2022.csv/ 0 1730908335000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2023.csv/ dim_drug_information_2023.csv/ 0 1730911121000 dbfs:/mnt/adverse-events/transformed-data/dim_drug_information_2024.csv/ dim_drug_information_2024.csv/ 0 1730913027000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2015.csv/ dim_patient_2015.csv/ 0 1730824426000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2016.csv/ dim_patient_2016.csv/ 0 1730826769000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2017.csv/ dim_patient_2017.csv/ 0 1730828519000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2018.csv/ dim_patient_2018.csv/ 0 1730832057000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2019.csv/ dim_patient_2019.csv/ 0 1730836289000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2020.csv/ dim_patient_2020.csv/ 0 1730838615000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2021.csv/ dim_patient_2021.csv/ 0 1730900115000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2022.csv/ dim_patient_2022.csv/ 0 1730907951000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2023.csv/ dim_patient_2023.csv/ 0 1730910763000 dbfs:/mnt/adverse-events/transformed-data/dim_patient_2024.csv/ dim_patient_2024.csv/ 0 1730912851000 dbfs:/mnt/adverse-events/transformed-data/dim_reaction_outcome.csv/ dim_reaction_outcome.csv/ 0 1730825047000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2015.csv/ dim_report_metadata_2015.csv/ 0 1730824870000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2016.csv/ dim_report_metadata_2016.csv/ 0 1730827285000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2017.csv/ dim_report_metadata_2017.csv/ 0 1730829052000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2018.csv/ dim_report_metadata_2018.csv/ 0 1730832667000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2019.csv/ dim_report_metadata_2019.csv/ 0 1730836937000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2020.csv/ dim_report_metadata_2020.csv/ 0 1730839314000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2021.csv/ dim_report_metadata_2021.csv/ 0 1730900817000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2022.csv/ dim_report_metadata_2022.csv/ 0 1730908675000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2023.csv/ dim_report_metadata_2023.csv/ 0 1730911438000 dbfs:/mnt/adverse-events/transformed-data/dim_report_metadata_2024.csv/ dim_report_metadata_2024.csv/ 0 1730913185000 dbfs:/mnt/adverse-events/transformed-data/dim_severity.csv/ dim_severity.csv/ 0 1730825048000 dbfs:/mnt/adverse-events/transformed-dat

In [0]:
directory_path = "dbfs:/mnt/adverse-events/transformed-data/"
files = dbutils.fs.ls(directory_path)

In [0]:
def concat_file_years(files, table_name, output_df):
    for file in files:
        if table_name in file.name:
            df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(file.path)
            if 'metadata' in table_name:
                year = (file.name.split('.')[0]).split('_')[3]
            else:
                year = (file.name.split('.')[0]).split('_')[2]
        
            df = df.withColumn('year', lit(year).cast(IntegerType()))
            output_df = output_df.union(df)
    return output_df


In [0]:
# dim_patient
dim_patient_schema = StructType([
    StructField("patient_id", IntegerType(), True),
    StructField("patient_onset_age", DoubleType(), True),
    StructField("patient_age_group", StringType(), True),
    StructField("patient_sex", StringType(), True),
    StructField("patient_weight(kg)", DoubleType(), True),
    StructField("year", IntegerType(), True)
])

In [0]:

# Create an empty DataFrame with the defined schema
combined_df = spark.createDataFrame([], schema=dim_patient_schema)
dim_patient = concat_file_years(files, 'dim_patient', combined_df)
display(dim_patient)




patient_id patient_onset_age patient_age_group patient_sex patient_weight(kg) year 10219568 80.0 Elderly Female null 2015 10444882 83.0 Elderly Female null 2015 10521631 1.0 Child Male null 2015 10595341 30.0 Adult Female 42.6 2015 10686463 57.0 Adult Female null 2015 10686464 49.0 Adult Male 122.45 2015 10686465 50.0 Adult Female null 2015 10686466 49.0 Adult Male null 2015 10686467 69.0 Elderly Female null 2015 10686468 63.0 Adult Male null 2015 10686469 64.0 Adult Female null 2015 10686470 47.0 Adult Female null 2015 10686471 73.0 Elderly Female null 2015 10686472 73.0 Elderly Female null 2015 10686473 70.0 Elderly Female null 2015 10686475 69.0 Elderly Male null 2015 10686477 57.0 Adult Male 67.6 2015 10686478 67.0 Elderly Male null 2015 10686479 37.0 Adult Male null 2015 10686480 74.0 Elderly Female null 2015 10686481 46.0 Adult Male null 2015 10686482 29.0 Adult Female null 2015 10686483 53.0 Adult Female null 2015 10686484 2.64 Child Male 81.6 2015 10686485 52.0 Adult Female null 2015 10686487 64.0 Adult Female null 2015 10686488 82.0 Elderly Female null 2015 10686489 6.0 Child Male null 2015 10686490 66.0 Elderly Male null 2015 10686493 94.0 Elderly Male null 2015 10686496 69.0 Elderly Unknown null 2015 10686497 65.0 Adult Female 65.0 2015 10686498 55.0 Adult Female null 2015 10686500 67.0 Elderly Female 67.12 2015 10686503 62.0 Adult Female null 2015 10686504 55.0 Adult Female null 2015 10686507 57.0 Adult Male null 2015 10686508 56.0 Adult Female null 2015 10686509 72.0 Elderly Female null 2015 10686510 55.0 Adult Female null 2015 10686511 56.0 Adult Female 104.3 2015 10686512 62.0 Adult Female null 2015 10686513 59.0 Adult Female null 2015 10686514 70.0 Elderly Female null 2015 10686515 68.0 Elderly Female null 2015 10686516 78.0 Elderly Female null 2015 10686519 64.0 Adult Female null 2015 10686520 45.0 Adult Female null 2015 10686521 54.0 Adult Female null 2015 10686522 67.0 Elderly Female null 2015 10686524 61.0 Adult Male null 2015 10686526 41.0 Adult Female null 2015 10686527 58.0 Adult Male null 2015 10686528 47.0 Adult Female null 2015 10686529 74.0 Elderly Male 62.0 2015 10686531 63.0 Adult Female null 2015 10686532 58.0 Adult Female null 2015 10686533 60.0 Adult Female null 2015 10686534 57.0 Adult Female null 2015 10686535 59.0 Adult Male null 2015 10686536 47.0 Adult Female null 2015 10686537 67.0 Elderly Male null 2015 10686538 64.0 Adult Female null 2015 10686543 41.0 Adult Female null 2015 10686544 51.0 Adult Female null 2015 10686545 50.0 Adult Female null 2015 10686547 43.0 Adult Female null 2015 10686548 61.0 Adult Female null 2015 10686549 58.0 Adult Female null 2015 10686551 57.0 Adult Female null 2015 10686552 43.0 Adult Female null 2015 10686553 63.0 Adult Female null 2015 10686554 43.0 Adult Female null 2015 10686555 50.0 Adult Female null 2015 10686556 57.0 Adult Male null 2015 10686557 38.0 Adult Female null 2015 10686558 0.0 Neonate Female null 2015 10686560 72.0 Elderly Female null 2015 10686561 29.0 Adult Female null 2015 10686562 66.0 Elderly Female null 2015 10686563 65.0 Adult Male null 2015 10686564 59.0 Adult Female null 2015 10686566 56.0 Adult Male null 2015 10686567 52.0 Adult Female null 2015 10686570 50.0 Adult Female null 2015 10686572 57.0 Adult Male null 2015 10686574 58.0 Adult Female null 2015 10686578 42.0 Adult Male null 2015 10686580 49.0 Adult Female null 2015 10686581 44.0 Adult Male null 2015 10686583 52.0 Adult Male null 2015 10686584 45.0 Adult Female 57.0 2015 10686585 66.0 Elderly Male null 2015 10686586 46.0 Adult Female null 2015 10686587 53.0 Adult Female null 2015 10686588 31.0 Adult Female null 2015 10686590 65.0 Adult Female null 2015 10686591 62.0 Adult Female null 2015 10686592 24.0 Adult Female null 2015 10686593 42.0 Adult Female null 2015 10686594 69.0 Elderly Female null 2015 10686596 75.0 Elderly Female null 2015 10686598 57.0 Adult Male null 2015 10686599 34.0 Adult Female null 2015 10686600 64.0 Adult Male null 2015 10686601 34.0 Adult Female null 20

In [0]:
# fact_reaction
fact_reaction_schema = StructType([
    StructField("patient_id", IntegerType(), True),
    StructField("patient_reaction", StringType(), True),
    StructField("reaction_outcome", IntegerType(), True),
    StructField("reaction_severity", IntegerType(), True),
    StructField("action_taken", IntegerType(), True),
    StructField("medicinal_product", StringType(), True),
    StructField("start_dosage_date", DateType(), True),
    StructField("action_taken", DateType(), True),
    StructField("year", IntegerType(), True)
])

In [0]:
combined_df = spark.createDataFrame([], schema=fact_reaction_schema)
fact_reaction = concat_file_years(files, 'fact_reaction', combined_df)
display(fact_reaction)

patient_id patient_reaction reaction_outcome reaction_severity action_taken medicinal_product start_dosage_date action_taken year 10686488 knee arthroplasty 1 4 4 advair null null 2015 10686490 bladder cancer 3 6 null bacillus 2013-12-06 null 2015 10686490 neuropathy peripheral 3 6 null bacillus 2013-12-06 null 2015 10686490 vascular cauterisation 1 6 null bacillus 2013-12-06 null 2015 10686490 neuralgia 3 6 null bacillus 2013-12-06 null 2015 10686490 pruritus 1 6 null bacillus 2013-12-06 null 2015 10686490 emergency care examination 1 6 null bacillus 2013-12-06 null 2015 10686490 blood urine present 1 6 null bacillus 2013-12-06 null 2015 10686493 myocardial infarction 5 1 null fluticasone 2011-08-15 null 2015 10686495 monoparesis 1 6 4 advair null null 2015 10686495 cerebrovascular accident 1 6 4 advair null null 2015 10686529 stomatitis 1 4 null rinderon 2014-03-17 2014-09-08 2015 10686529 white blood cell count decreased 1 4 null rinderon 2014-06-18 2014-09-08 2015 10686529 platelet count decreased 1 4 null rinderon 2014-04-15 2014-06-17 2015 10686529 vertigo positional 1 4 null rinderon 2014-04-01 2014-04-14 2015 10686529 rash erythematous 1 4 null rinderon 2014-04-01 2014-04-14 2015 10686529 haemoglobin decreased 3 4 null rinderon 2014-04-01 2014-09-08 2015 10686584 flushing 1 4 null vianimithe 1994-01-01 null 2015 10686584 multiple sclerosis relapse 3 4 null vianimithe 2008-01-01 null 2015 10686584 rehabilitation therapy 6 4 null vianimithe 1994-01-01 null 2015 10686684 paranasal sinus hypersecretion 2 7 4 wellbutrin null null 2015 10686684 nasopharyngitis 2 7 4 wellbutrin null null 2015 10686700 condition aggravated 5 1 null fluticasone 2014-11-17 null 2015 10686700 pulmonary fibrosis 5 1 null fluticasone 2014-11-17 null 2015 10686705 neoplasm malignant 6 6 5 advair null null 2015 10686705 coma 6 6 5 advair null null 2015 10686705 tracheostomy 6 6 5 advair null null 2015 10686705 respiratory failure 6 6 5 advair null null 2015 10686734 febrile neutropenia 1 4 null calcium 2014-11-03 2014-11-06 2015 10686770 off label use 6 7 null amlodipine null null 2015 10686770 skin odour abnormal 3 7 null amlodipine null null 2015 10686788 dizziness 3 7 1 nicoderm null null 2015 10686788 tinnitus 1 7 1 nicoderm null null 2015 10686788 confusional state 3 7 1 nicoderm null null 2015 10686788 headache 1 7 1 nicoderm null null 2015 10686788 memory impairment 3 7 1 nicoderm null null 2015 10686788 throat tightness 1 7 1 nicoderm null null 2015 10686788 overdose 1 7 1 nicoderm null null 2015 10686858 abdominal pain 6 4 6 amlodipine null null 2015 10686858 intentional overdose 6 4 6 amlodipine null null 2015 10686858 drug level increased 1 4 6 amlodipine null null 2015 10686858 distributive shock 6 4 6 amlodipine null null 2015 10686858 hypotension 2 4 6 amlodipine null null 2015 10686858 arrhythmia 1 4 6 amlodipine null null 2015 10686858 nausea 6 4 6 amlodipine null null 2015 10686891 intentional product misuse 6 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 viral infection 6 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 blood pressure diastolic increased 3 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 diarrhoea 6 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 pyrexia 3 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 asthma 6 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 back pain 6 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 arthralgia 6 7 4 nexium 2014-12-19 2014-12-19 2015 10686891 faeces discoloured 3 7 4 nexium 2014-12-19 2014-12-19 2015 10686991 upper limb fracture 6 6 4 alendronic null null 2015 10686991 drug dose omission 6 6 4 alendronic null null 2015 10687065 drug ineffective 6 7 null ibuprofen null null 2015 10687065 product quality issue 6 7 null ibuprofen null null 2015 10687116 lip swelling 1 7 1 ibuprofen null null 2015 10687116 pruritus 1 7 1 ibuprofen null null 2015 10687128 drug ineffective 3 7 4 nexium null null 2015 10687128 dyspepsia 3 7 4 nexium null null 2015 10687199 myocardial infarction 1 4 1 olmetec nul

In [0]:
# dim_patient
dim_report_metadata_schema = StructType([
    StructField("safety_report_id", IntegerType(), True),
    StructField("occurance_country", StringType(), True),
    StructField("date_report_received", DateType(), True),
    StructField("date_of_transmission", DateType(), True),
    StructField("reported_company", StringType(), True),
    StructField("year", IntegerType(), True)
])

In [0]:
combined_df = spark.createDataFrame([], schema=dim_report_metadata_schema)
dim_report_metadata = concat_file_years(files, 'dim_report_metadata', combined_df)
display(dim_report_metadata)

safety_report_id occurance_country date_report_received date_of_transmission reported_company year 10219568 US 2015-07-05 2015-11-25 glaxosmithkline 2015 10444882 IL 2015-08-11 2015-11-25 actelion 2015 10521631 US 2015-01-15 2015-11-25 lundbeck 2015 10595341 null 2015-03-09 2016-03-04 0199 2015 10686463 US 2015-01-01 2015-07-20 amgen 2015 10686464 US 2015-01-01 2015-07-20 amgen 2015 10686465 US 2015-01-01 2015-07-20 amgen 2015 10686466 US 2015-01-01 2015-07-20 amgen 2015 10686467 US 2015-01-01 2015-07-20 astrazeneca 2015 10686468 US 2015-01-01 2016-03-04 roche 2015 10686469 US 2015-01-01 2020-07-13 amgen 2015 10686470 US 2015-01-01 2015-07-20 amgen 2015 10686471 US 2015-01-01 2015-07-20 amgen 2015 10686472 US 2015-01-01 2015-07-20 amgen 2015 10686473 US 2015-01-01 2015-07-20 amgen 2015 10686474 PE 2015-01-01 2015-07-20 roche 2015 10686475 US 2015-01-01 2015-07-20 amgen 2015 10686476 US 2015-01-01 2015-07-20 astrazeneca 2015 10686477 CA 2015-01-01 2016-05-25 roche 2015 10686478 US 2015-01-01 2015-07-20 amgen 2015 10686479 BR 2015-01-01 2015-07-20 lundbeck 2015 10686480 US 2015-01-01 2015-07-20 astrazeneca 2015 10686481 US 2015-01-01 2015-07-20 amgen 2015 10686482 US 2015-01-01 2016-03-04 amgen 2015 10686483 US 2015-01-01 2015-07-20 amgen 2015 10686484 US 2015-01-01 2015-07-20 astrazeneca 2015 10686485 US 2015-01-01 2015-07-20 amgen 2015 10686486 US 2015-01-01 2015-07-20 b i pharmaceuticals /ridgefield 2015 10686487 US 2015-01-01 2015-07-20 amgen 2015 10686488 US 2015-01-01 2015-07-20 glaxosmithkline 2015 10686489 US 2015-01-01 2015-07-20 glaxosmithkline 2015 10686490 US 2015-01-01 2016-05-25 glaxosmithkline 2015 10686491 US 2015-01-01 2016-05-25 glaxosmithkline 2015 10686492 US 2015-01-01 2015-08-21 glaxosmithkline 2015 10686493 PE 2015-01-01 2015-07-20 glaxosmithkline 2015 10686494 US 2015-01-01 2015-11-25 glaxosmithkline 2015 10686495 US 2015-01-01 2015-07-20 glaxosmithkline 2015 10686496 US 2015-01-01 2015-07-20 glaxosmithkline 2015 10686497 CO 2015-01-01 2015-07-20 roche 2015 10686498 US 2015-01-01 2015-07-20 amgen 2015 10686499 US 2015-01-01 2015-07-20 roche 2015 10686500 GB 2015-01-01 2020-11-05 roche 2015 10686501 null 2015-01-01 2022-07-20 roche 2015 10686502 US 2015-01-01 2015-07-20 roche 2015 10686503 US 2015-01-01 2015-07-20 amgen 2015 10686504 US 2015-01-01 2015-07-20 amgen 2015 10686505 US 2015-01-01 2015-07-20 astrazeneca 2015 10686506 AT 2015-01-01 2015-07-20 astrazeneca 2015 10686507 US 2015-01-01 2015-07-20 amgen 2015 10686508 GB 2015-01-01 2015-07-20 abbvie 2015 10686509 US 2015-01-01 2015-07-20 amgen 2015 10686510 US 2015-01-01 2015-07-20 amgen 2015 10686511 US 2015-01-01 2015-07-20 amgen 2015 10686512 US 2015-01-01 2015-07-20 amgen 2015 10686513 BR 2015-01-01 2015-07-20 amgen 2015 10686514 JP 2015-01-01 2015-07-20 roche 2015 10686515 AU 2015-01-01 2015-07-20 roche 2015 10686516 US 2015-01-01 2015-07-20 amgen 2015 10686517 US 2015-01-01 2015-07-20 astrazeneca 2015 10686518 US 2015-01-01 2015-07-20 astrazeneca 2015 10686519 US 2015-01-01 2015-07-20 amgen 2015 10686520 US 2015-01-01 2015-07-20 amgen 2015 10686521 US 2015-01-01 2015-07-20 amgen 2015 10686522 US 2015-01-01 2015-07-20 amgen 2015 10686523 US 2015-01-01 2015-07-20 amgen 2015 10686524 US 2015-01-01 2015-07-20 amgen 2015 10686525 US 2015-01-01 2015-07-20 astrazeneca 2015 10686526 US 2015-01-01 2015-07-20 amgen 2015 10686527 GB 2015-01-01 2015-07-20 amgen 2015 10686528 US 2015-01-01 2015-07-20 amgen 2015 10686529 JP 2015-01-01 2015-07-20 roche 2015 10686530 GB 2015-01-01 2015-11-25 amgen 2015 10686531 US 2015-01-01 2015-07-20 amgen 2015 10686532 US 2015-01-01 2015-07-20 amgen 2015 10686533 US 2015-01-01 2015-07-20 amgen 2015 10686534 US 2015-01-01 2015-07-20 amgen 2015 10686535 BR 2015-01-01 2015-07-20 roche 2015 10686536 IT 2015-01-01 2015-07-20 biogenidec 2015 10686537 US 2015-01-01 2015-11-25 biogenidec 2015 10686538 US 2015-01-01 2015-07-20 biogenidec 2015 10686539 US 2015-01-01 2015-07-20 biogenidec 2015 10686540 US 2015-01-01 2015-07-20 biogenide

In [0]:
def concat_drug_info(files, table_name, output_df):
    for file in files:
        if table_name in file.name:
            df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(file.path)
            output_df = output_df.union(df)
    return output_df

In [0]:
# dim_patient
dim_drug_schema = StructType([
    StructField("medicinal_product", StringType(), True),
    StructField("indication", StringType(), True),
    StructField("administration_route", IntegerType(), True),
    StructField("dosage_form", StringType(), True)
])

In [0]:
combined_df = spark.createDataFrame([], schema=dim_drug_schema)
dim_drug_information = concat_drug_info(files, 'dim_drug_information', combined_df)
dim_drug_information = dim_drug_information.dropDuplicates(['medicinal_product'])
display(dim_drug_information)

medicinal_product indication administration_route dosage_form aaoluona neoplasm malignant 41 injection abasaglar type 2 diabetes mellitus 58 null abataceptgenetical rheumatoid arthritis 58 injection abcid gastrooesophageal reflux disease 48 null abella contraception 48 tablet abirateron prostate cancer metastatic 48 tablet abiraterona prostate cancer metastatic 65 null abitrexate lymphomatoid papulosis 48 null ablok product used for unknown indication 65 null abrilada ankylosing spondylitis 58 null absorcol hypercholesterolaemia null tablet abtei product used for unknown indication 65 null abuteral null 48 null abuterol null null inhalant acalabrutimib product used for unknown indication null null acamol migraine null null acanthopanax therapeutic procedure 41 injection acara osteoporosis 48 null acarbose type 2 diabetes mellitus 48 tablet acard polycythaemia vera 48 null acarizax mite allergy null oral lyophilisate acatar null 45 null accorduk product used for unknown indication null null accredo null 48 null accrete product used for unknown indication null null acecor null null tablets acedip product used for unknown indication 65 tablet acediur product used for unknown indication 48 null acefen arthritis 65 unknown aceil cardiovascular event prophylaxis 48 null acelio general anaesthesia 42 null acelisino hypertension 65 null aceoto infection prophylaxis 48 unknown acertanlo hypertension 65 tablet acesulfame product used for unknown indication null null acetamide product used for unknown indication null null acetamin product used for unknown indication 65 tablet acetaminoph pain null null acetaminophencodei product used for unknown indication null null acetaminophenhyd mental disorder 65 null acetaminophn product used for unknown indication null null acetate dehydration 65 null acetated pyelonephritis acute null null acetazolamide product used for unknown indication null tablet acetazolomide product used for unknown indication 48 capsule acetil null 48 null acetisalicilico thrombosis prophylaxis 48 null acetminophen sleep disorder 65 tablet acetonido product used for unknown indication 61 null acetulsalicylic product used for unknown indication null null acetutolol product used for unknown indication 48 null acetylcholine product used for unknown indication null powder acetylcystein null null dispersible tablet acetylcysteinefolic product used for unknown indication 48 null acetylcystenine chest discomfort 48 granulate acetylic product used for unknown indication null null acetylsaclicylic product used for unknown indication null tablet acetylsalicalic product used for unknown indication null null acetylsalicic product used for unknown indication 65 null acetylsalicyc null 48 tablet acetylsalicylitoc prophylaxis 48 tablet acetylsalicylsyra null 48 tablet acetylsalicytado product used for unknown indication 48 null acetylsalisylic null 65 null acetylsalisylsyre product used for unknown indication null null acetylsaliycylic chest pain null null acetylsalycylic thrombosis prophylaxis 48 null achillea constipation 48 granule achyranthes null 48 granule aciclor product used for unknown indication 65 null aciclovirinterferon opportunistic infection prophylaxis 48 null acidi vitamin supplementation 48 null acidil null null tablet acidun nervous system disorder prophylaxis 48 null aciferol vitamin supplementation 48 null acifix product used for unknown indication 65 null acifol product used for unknown indication 65 tablet aciloc null 65 null acipan null 48 null aclatonium null 48 capsule aclometasone eczema null null aclotine null 42 null aclova herpes zoster 42 injection acnetrait acne 48 capsule, soft aconitum null 48 sublingual tablet acorus foetal exposure during pregnancy 64 null acovil null 48 tablet acrinol infusion site extravasation 3 poultice or patch actage null null tablets actar product used for unknown indication 65 unknown actaviss null 65 tablet acteaminophen product used for unknown indication null tablets actein 

In [0]:
fact_reaction.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/consumer-data/fact_reaction.csv")
dim_patient.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/consumer-data/dim_patient.csv")
dim_drug_information.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/consumer-data/dim_drug_information.csv")
dim_report_metadata.repartition(1).write.mode("overwrite").option("header", "true").csv(f"mnt/adverse-events/consumer-data/dim_report_metadata.csv")